Une seule consigne, remplissez le fichier afin de reproduire le comportement de l'exercice 01, je laisse toute les sortie mais si vous executez vous perdez le contenu de la cellule.

In [1]:
!pip install owlready2
from owlready2 import *
default_world.set_backend(filename = "file_back1.sqlite3", exclusive = False)

In [50]:
import pandas as pd
import numpy as np
df = pd.read_csv("netflix_titles.csv")
df = df.rename(columns={'listed_in':'categorie'})

#hésitez pas a diminuer ce chiffre pour executer plus rapidement l'inférence
df = df.head(150)
print(np.array(df).shape)

def get_actors_names(cast):
    name = str(cast)
    names = name.split(",")
    l = []
    for i in names:
        n = i.split(" ")
        nn = []
        for i in n:
            if(i!=""):
                nn.append(i)
        l.append(nn)
    actors= []
    for i in l:
        actors.append( tuple([i[-1]," ".join(i[:-1])]))
    return actors

actors_set = set()
for i in df["cast"]:
    actors = get_actors_names(i)
    actors_set.update(set(actors))

actors_set= list(actors_set)
print("Nombre d'acteurs : ",len(actors_set))
print(df.head())

(150, 12)
Nombre d'acteurs :  933
    show_id     type                                    title  \
0  81145628    Movie  Norm of the North: King Sized Adventure   
1  80117401    Movie               Jandino: Whatever it Takes   
2  70234439  TV Show                       Transformers Prime   
3  80058654  TV Show         Transformers: Robots in Disguise   
4  80125979    Movie                             #realityhigh   

                   director  \
0  Richard Finn, Tim Maltby   
1                       NaN   
2                       NaN   
3                       NaN   
4          Fernando Lebrija   

                                                cast  \
0  Alan Marriott, Andrew Toth, Brian Dobson, Cole...   
1                                   Jandino Asporaat   
2  Peter Cullen, Sumalee Montano, Frank Welker, J...   
3  Will Friedle, Darren Criss, Constance Zimmer, ...   
4  Nesta Cooper, Kate Walsh, John Michael Higgins...   

                                    country        

In [51]:
#Créer une nouvelle ontologie
onto = get_ontology("http://test.org/onto.owl")

In [52]:
with onto:
    
    class Acteur(Thing):
        pass
    
    class Contenu(Thing):
        pass
    
    class Film(Contenu):
        pass
    
    class type_contenu(Contenu >> str):
        pass
    
    class givenName(Acteur >> str):
        pass
    
    class familyName(Acteur >> str):
        pass
    
    class description(Contenu >> str):
        pass
    
    class title(Contenu >> str):
        pass
    
    class releaseYear(Contenu >> int):
        pass
    class knows(Acteur >> Acteur):
        pass
    class playedIn(ObjectProperty):
        domain    = [Acteur]
        range     = [Contenu]
    
    class Acteur_a_Succes(Thing):
        equivalent_to = [Acteur & playedIn.only(Film)]


In [53]:
actors = {}
for nom,prenom in actors_set:
    A = Acteur()
    actors[(nom,prenom)] = A
    A.givenName.append(prenom)
    A.familyName.append(nom)
print(A.givenName)

['Kate']


In [54]:

onto.save(file = "out.owl", format = "ntriples")
!cat out.owl

<http://test.org/onto.owl> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Ontology> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Film> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Film> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://test.org/onto.owl#Contenu> .
<http://test.org/onto.owl#type_contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#DatatypeProperty> .


<http://test.org/onto.owl#acteur568> <http://test.org/onto.owl#givenName> "Sissi"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur568> <http://test.org/onto.owl#familyName> "Duparc"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur569> <http://test.org/onto.owl#givenName> "Rachel"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur569> <http://test.org/onto.owl#familyName> "Staman"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur570> <http://test.org/onto.owl#givenName> "Damian"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur570> <http://test.org/onto.owl#familyName> "Woetzel"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur571> <http://test.org/onto.owl#givenName> "Ge"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur571> <http://test.org/onto.owl#familyName> "Wang"^^<http://www.w3.org/200

In [55]:
films_dict = {}
arr = np.array(df)
for idd,type_f,title,description in zip(arr[:,0],arr[:,1],arr[:,2],arr[:,-1]):
    if(type_f == "Movie"):
        F = Film()
    else:
        F = Contenu()
    F.title.append(title)
    F.description.append(description)
    F.type_contenu.append(type_f)
    films_dict[idd] = F

In [56]:
onto.save(file = "out.owl", format = "ntriples")
!cat out.owl

<http://test.org/onto.owl> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Ontology> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Film> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Film> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://test.org/onto.owl#Contenu> .
<http://test.org/onto.owl#type_contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#DatatypeProperty> .


<http://test.org/onto.owl#acteur568> <http://test.org/onto.owl#givenName> "Sissi"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur568> <http://test.org/onto.owl#familyName> "Duparc"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur569> <http://test.org/onto.owl#givenName> "Rachel"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur569> <http://test.org/onto.owl#familyName> "Staman"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur570> <http://test.org/onto.owl#givenName> "Damian"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur570> <http://test.org/onto.owl#familyName> "Woetzel"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur571> <http://test.org/onto.owl#givenName> "Ge"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur571> <http://test.org/onto.owl#familyName> "Wang"^^<http://www.w3.org/200

In [57]:
for acteur_list, ids in zip(df["cast"],df["show_id"]):
    Lacc = get_actors_names(acteur_list)
    film=films_dict[ids]
    for i in Lacc:
        actors[i].playedIn.append(film)

In [58]:
onto.save(file = "out.owl", format = "ntriples")
!cat out.owl

<http://test.org/onto.owl> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Ontology> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Film> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Film> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://test.org/onto.owl#Contenu> .
<http://test.org/onto.owl#type_contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#DatatypeProperty> .


<http://test.org/onto.owl#acteur137> <http://test.org/onto.owl#familyName> "Froseth"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur138> <http://test.org/onto.owl#givenName> "Chang"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur138> <http://test.org/onto.owl#familyName> "Chen"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur139> <http://test.org/onto.owl#givenName> "Jennifer"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur139> <http://test.org/onto.owl#familyName> "Lafleur"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur140> <http://test.org/onto.owl#givenName> "Thomas"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur140> <http://test.org/onto.owl#familyName> "Cocquerel"^^<http://www.w3.org/2001/XMLSchema#string> .
<http://test.org/onto.owl#acteur141> <http://test.org/onto.owl#givenName> "Zach"^^<http://www.w3

In [59]:
with onto:
    sync_reasoner()

* Owlready2 * Running HermiT...
    java -Xmx2000M -cp /home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/hermit:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/hermit/HermiT.jar org.semanticweb.HermiT.cli.CommandLine -c -O -D -I file:////tmp/tmplz0bbxnq
* Owlready2 * HermiT took 119.27414846420288 seconds
* Owlready * (NB: only changes on entities loaded in Python are shown, other changes are done but not listed)


In [60]:
onto.save(file = "out.owl", format = "ntriples")
!cat out.owl

<http://test.org/onto.owl> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Ontology> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Acteur> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Contenu> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://www.w3.org/2002/07/owl#Thing> .
<http://test.org/onto.owl#Film> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://test.org/onto.owl#Film> <http://www.w3.org/2000/01/rdf-schema#subClassOf> <http://test.org/onto.owl#Contenu> .
<http://test.org/onto.owl#type_contenu> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#DatatypeProperty> .


<http://test.org/onto.owl#acteur670> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film124> .
<http://test.org/onto.owl#acteur757> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film124> .
<http://test.org/onto.owl#acteur813> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film124> .
<http://test.org/onto.owl#acteur722> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film124> .
<http://test.org/onto.owl#acteur789> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film124> .
<http://test.org/onto.owl#acteur734> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film125> .
<http://test.org/onto.owl#acteur520> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film125> .
<http://test.org/onto.owl#acteur144> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film125> .
<http://test.org/onto.owl#acteur231> <http://test.org/onto.owl#playedIn> <http://test.org/onto.owl#film125> .
<http://te

In [61]:
A = onto.search(type = Acteur)
for a in A:
    print(a.playedIn)

[onto.contenu1, onto.contenu2]
[onto.film9, onto.film10, onto.film11]
[onto.contenu3]
[onto.contenu1]
[onto.film6]
[onto.contenu1]
[onto.contenu1]
[onto.film6]
[onto.contenu2]
[onto.film7]
[onto.contenu2]
[onto.film5]
[onto.film3]
[onto.film4]
[onto.film6]
[onto.film4]
[onto.film1]
[onto.film6]
[onto.contenu3]
[onto.contenu2]
[onto.film3]
[onto.film1]
[onto.film6]
[onto.film3]
[onto.film3]
[onto.film6]
[onto.film3]
[onto.contenu3]
[onto.film4]
[onto.film1]
[onto.film8]
[onto.film6]
[onto.film4]
[onto.film8]
[onto.film2]
[onto.film8]
[onto.film1]
[onto.contenu2]
[onto.film4]
[onto.film8]
[onto.film3]
[onto.contenu1]
[onto.film3]
[onto.film4]
[onto.film8]
[onto.film1]
[onto.film8]
[onto.contenu1]
[onto.contenu2]
[onto.film3]
[onto.contenu2]
[onto.contenu1]
[onto.film1]
[onto.film3]
[onto.film9, onto.film10]
[onto.film6]
[onto.film4]
[onto.film4]
[onto.film4]
[onto.film1]
[onto.film3]
[onto.film9, onto.film10, onto.film11]
[onto.contenu1]
[onto.film3]
[onto.contenu4]
[onto.film1]
[onto.fi

[onto.film122]
[onto.film43]
[onto.film83]
[onto.film37]
[onto.film119]
[onto.contenu14]
[onto.film84]
[onto.film115]
[onto.film120]
[onto.film126]
[onto.film114]
[onto.contenu23]
[onto.contenu34]
[onto.film32]
[onto.film45]
[onto.film89]
[onto.film84]
[onto.film105]
[onto.film78]
[onto.contenu8, onto.film30, onto.film34, onto.contenu10, onto.contenu17, onto.contenu18, onto.contenu19, onto.contenu20, onto.contenu22, onto.film67, onto.film72, onto.film74, onto.film76, onto.film82, onto.contenu27, onto.film86, onto.film87, onto.film90, onto.film99, onto.film100, onto.film107, onto.film116, onto.contenu36]
[onto.film106]
[onto.film83]
[onto.contenu13]
[onto.film19]
[onto.film62]
[onto.contenu9]
[onto.film61]
[onto.film78]
[onto.film19]
[onto.film70]
[onto.film101]
[onto.contenu29]
[onto.film44]
[onto.film44]
[onto.film42]
[onto.film62]
[onto.film29]
[onto.film41]
[onto.film40]
[onto.contenu33]
[onto.film119]
[onto.film58]
[onto.film124, onto.film127]
[onto.film69]
[onto.contenu34]
[onto.f

In [62]:
with onto:
    rule = Imp()
    rule.set_as_rule("""Acteur(?a1), Acteur(?a2), playedIn(?a1, ?f1), playedIn(?a2, ?f1) -> knows(?a1, ?a2)""")

In [63]:
with onto:
    sync_reasoner(infer_property_values = True)
    sync_reasoner_pellet(infer_property_values = True)

* Owlready2 * Running HermiT...
    java -Xmx2000M -cp /home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/hermit:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/hermit/HermiT.jar org.semanticweb.HermiT.cli.CommandLine -c -O -D -I file:////tmp/tmp9bukgrfs -Y
* Owlready2 * HermiT took 118.15996193885803 seconds


* Owlready * Adding relation onto.acteur641 knows onto.acteur641
* Owlready * Adding relation onto.acteur641 knows onto.acteur1008
* Owlready * Adding relation onto.acteur641 knows onto.acteur1014
* Owlready * Adding relation onto.acteur641 knows onto.acteur373
* Owlready * Adding relation onto.acteur641 knows onto.acteur929
* Owlready * Adding relation onto.acteur641 knows onto.acteur201
* Owlready * Adding relation onto.acteur641 knows onto.acteur667
* Owlready * Adding relation onto.acteur641 knows onto.acteur229
* Owlready * Adding relation onto.acteur641 knows onto.acteur245
* Owlready * Adding relation onto.acteur641 knows onto.acteur806
* Owlready * Adding relation onto.acteur641 knows onto.acteur495
* Owlready * Adding relation onto.acteur310 knows onto.acteur585
* Owlready * Adding relation onto.acteur310 knows onto.acteur310
* Owlready * Adding relation onto.acteur310 knows onto.acteur447
* Owlready * Adding relation onto.acteur310 knows onto.acteur510
* Owlready * Adding rel

* Owlready * Adding relation onto.acteur221 knows onto.acteur533
* Owlready * Adding relation onto.acteur221 knows onto.acteur162
* Owlready * Adding relation onto.acteur221 knows onto.acteur875
* Owlready * Adding relation onto.acteur221 knows onto.acteur321
* Owlready * Adding relation onto.acteur221 knows onto.acteur619
* Owlready * Adding relation onto.acteur221 knows onto.acteur607
* Owlready * Adding relation onto.acteur221 knows onto.acteur221
* Owlready * Adding relation onto.acteur221 knows onto.acteur319
* Owlready * Adding relation onto.acteur329 knows onto.acteur1013
* Owlready * Adding relation onto.acteur329 knows onto.acteur89
* Owlready * Adding relation onto.acteur329 knows onto.acteur605
* Owlready * Adding relation onto.acteur329 knows onto.acteur329
* Owlready * Adding relation onto.acteur329 knows onto.acteur826
* Owlready * Adding relation onto.acteur329 knows onto.acteur599
* Owlready * Adding relation onto.acteur329 knows onto.acteur719
* Owlready * Adding relat

* Owlready * Adding relation onto.acteur742 knows onto.acteur524
* Owlready * Adding relation onto.acteur742 knows onto.acteur635
* Owlready * Adding relation onto.acteur742 knows onto.acteur742
* Owlready * Adding relation onto.acteur742 knows onto.acteur331
* Owlready * Adding relation onto.acteur742 knows onto.acteur707
* Owlready * Adding relation onto.acteur742 knows onto.acteur115
* Owlready * Adding relation onto.acteur654 knows onto.acteur372
* Owlready * Adding relation onto.acteur654 knows onto.acteur172
* Owlready * Adding relation onto.acteur654 knows onto.acteur117
* Owlready * Adding relation onto.acteur654 knows onto.acteur654
* Owlready * Adding relation onto.acteur654 knows onto.acteur419
* Owlready * Adding relation onto.acteur654 knows onto.acteur890
* Owlready * Adding relation onto.acteur654 knows onto.acteur627
* Owlready * Adding relation onto.acteur654 knows onto.acteur460
* Owlready * Adding relation onto.acteur654 knows onto.acteur880
* Owlready * Adding relat

* Owlready * Adding relation onto.acteur613 knows onto.acteur303
* Owlready * Adding relation onto.acteur613 knows onto.acteur291
* Owlready * Adding relation onto.acteur613 knows onto.acteur965
* Owlready * Adding relation onto.acteur613 knows onto.acteur405
* Owlready * Adding relation onto.acteur613 knows onto.acteur452
* Owlready * Adding relation onto.acteur397 knows onto.acteur840
* Owlready * Adding relation onto.acteur397 knows onto.acteur397
* Owlready * Adding relation onto.acteur397 knows onto.acteur581
* Owlready * Adding relation onto.acteur397 knows onto.acteur802
* Owlready * Adding relation onto.acteur397 knows onto.acteur819
* Owlready * Adding relation onto.acteur397 knows onto.acteur648
* Owlready * Adding relation onto.acteur397 knows onto.acteur803
* Owlready * Adding relation onto.acteur397 knows onto.acteur486
* Owlready * Adding relation onto.acteur397 knows onto.acteur403
* Owlready * Adding relation onto.acteur397 knows onto.acteur499
* Owlready * Adding relat

* Owlready * (NB: only changes on entities loaded in Python are shown, other changes are done but not listed)
* Owlready2 * Running Pellet...
    java -Xmx2000M -cp /home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/jcl-over-slf4j-1.6.4.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/jena-tdb-0.10.0.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/xercesImpl-2.10.0.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/aterm-java-1.6.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/antlr-runtime-3.2.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/jgrapht-jdk1.5.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/commons-codec-1.6.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/jena-iri-0.9.5.jar:/home/mohamed/anaconda3/lib/python3.7/site-packages/owlready2/pellet/httpcore-4.2.2.jar:/home/mohamed/anaconda3/lib

OwlReadyJavaError: Java error message is:
log4j:WARN No appenders could be found for logger (com.hp.hpl.jena.sparql.mgt.ARQMgt).
log4j:WARN Please initialize the log4j system properly.
log4j:WARN See http://logging.apache.org/log4j/1.2/faq.html#noconfig for more info.
Classifying 6 elements
Classifying:  16% complete in 00:00Classifying:  33% complete in 00:00Classifying:  50% complete in 00:00Classifying:  66% complete in 00:00Classifying:  83% complete in 00:00Classifying:  100% complete in 00:00
Classifying finished in 00:00
Realizing 6 elements
Realizing:  16% complete in 00:00Realizing:  33% complete in 00:00Realizing:  50% complete in 00:00Exception in thread "main" java.lang.OutOfMemoryError: Java heap space: failed reallocation of scalar replaced objects


In [64]:
onto.save(file = "out.owl")
!cat out.owl
default_world.save()

<?xml version="1.0"?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#"
         xmlns:xsd="http://www.w3.org/2001/XMLSchema#"
         xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#"
         xmlns:owl="http://www.w3.org/2002/07/owl#"
         xml:base="http://test.org/onto.owl"
         xmlns="http://test.org/onto.owl#"
         xmlns:swrl="http://www.w3.org/2003/11/swrl#">

<owl:Ontology rdf:about="http://test.org/onto.owl"/>

<owl:ObjectProperty rdf:about="#knows">
  <rdfs:domain rdf:resource="#Acteur"/>
  <rdfs:range rdf:resource="#Acteur"/>
</owl:ObjectProperty>

<owl:ObjectProperty rdf:about="#playedIn">
  <rdfs:domain rdf:resource="#Acteur"/>
  <rdfs:range rdf:resource="#Contenu"/>
</owl:ObjectProperty>

<owl:DatatypeProperty rdf:about="#type_contenu">
  <rdfs:domain rdf:resource="#Contenu"/>
  <rdfs:range rdf:resource="http://www.w3.org/2001/XMLSchema#string"/>
</owl:DatatypeProperty>

<owl:DatatypeProperty rdf:about="#givenName">
  <rdfs:domain rdf:resource=

  <playedIn rdf:resource="#film54"/>
  <givenName rdf:datatype="http://www.w3.org/2001/XMLSchema#string">Sivagorn</givenName>
  <familyName rdf:datatype="http://www.w3.org/2001/XMLSchema#string">Muttamara</familyName>
</Acteur>

<Acteur rdf:about="#acteur791">
  <rdf:type rdf:resource="http://www.w3.org/2002/07/owl#NamedIndividual"/>
  <knows rdf:resource="#acteur413"/>
  <knows rdf:resource="#acteur616"/>
  <knows rdf:resource="#acteur189"/>
  <knows rdf:resource="#acteur568"/>
  <knows rdf:resource="#acteur746"/>
  <knows rdf:resource="#acteur718"/>
  <knows rdf:resource="#acteur549"/>
  <knows rdf:resource="#acteur612"/>
  <knows rdf:resource="#acteur791"/>
  <knows rdf:resource="#acteur449"/>
  <playedIn rdf:resource="#film38"/>
  <givenName rdf:datatype="http://www.w3.org/2001/XMLSchema#string">Anna</givenName>
  <familyName rdf:datatype="http://www.w3.org/2001/XMLSchema#string">Mouglalis</familyName>
</Acteur>

<Acteur rdf:about="#acteur792">
  <rdf:type rdf:resource="http://www.

In [65]:
graph = default_world.as_rdflib_graph()

In [66]:
requete = """
prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?nom ?prenom
WHERE{
?s rdf:type :Acteur . 
?s :givenName ?nom . 
?s :familyName ?prenom
}
"""
print(requete)
res = graph.query(requete)
for i in res:
    print(str(i[0]),str(i[1]))


prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?nom ?prenom
WHERE{
?s rdf:type :Acteur . 
?s :givenName ?nom . 
?s :familyName ?prenom
}

Will Friedle
Damandeep Singh Baggan
Claudia Traisac
Ernie Hudson
Omar Sy
Jeffrey Combs
Sumalee Montano
Michael Jibson
Mitchell Whitfield
Joaquín Reyes
Khary Payton
Fabrizio Copano
Kid Ink
Christa Campbell
Oliver Dimsdale
Birgitte Hjort Sørensen
Alan Marriott
Sam Spruell
Lucía Jiménez
Darren Criss
Patrick Davis
Lee Tockar
Diana Hardcastle
Keith Powers
Yousef Erakat
Anna Friel
Kate Walsh
Verónica Echegui
Tim McInnerny
Cole Howard
Jim Sturgess
Tom Wilkinson
Dylan McDermott
Sam Worthington
Jandino Asporaat
David Dencik
Maya Kay
Stuart Allan
Andy Nyman
Ryan Kwanten
Nesta Cooper
Tania Gunadi
Alicia Sanz
Melanie Griffith
Thomas Cocquerel
Jonathan Holmes
Anthony Hopkins
Steve Blum
Constance Zimmer


Pam Rose
Anita Hara
Chindavanich Primrose
Mishael Morgan
Li Ai
Yolonda Ross
 Suman
Kid Capri
Tom O'Brien
Billy Zane
Florence Kasumba
Tony Todd
Craig Gazey
Joely Richardson
Wendee Lee
David Campbell
Amy Pietz
Déborah Révy
Vennela Kishore
Maggie Grace
Jonathan Whitesell
Kevin Bishop
Viineet Kumar
Bianca Hello
Kai Calhoun
Babe Cabita
Sobhita Dhulipala
Achita Sikamana
André Holland
 Aishwarya
Maddie Ziegler
Ryosuke Yusa
Sutatta Udomsilp
Giovanni Ribisi
Micah Stock
Natalie Dormer
 iLLBLISS
Nora Danish
Byeong-eun Park
Hidetoshi Hoshida
Alexander Skarsgård
Zhao Benshan
Seu Jorge
Marsha Wattanapanich
Ungsumalynn Sirapatsakmetha
Mert Öner
 Nimo
Billy Boyd
 Rukhsar
Mohammed Azaay
Sutthatip Wutichaipradit
Wang Zijian
Tiaré Scanda
Deepak Damle
Jesse Rath
Christopher Schärf
Ophelia Lovibond
Carmen Machi
Ron Perlman
Michaela Watkins
Rermthon Kemapech
Sushanth Reddy
So-ri Moon
Ken Hudson Campbell
Tim Blake Nelson
Rasmus Hardiker
Keanu Reeves
Tantoo Cardinal
Kat Gellin
Joel Dommett
Lee Seung-gi
Daryl 

In [68]:
import rdflib
graphe2 = rdflib.Graph()
graphe2.parse("out.owl")
requete = """
prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?s ?p ?o
WHERE{
?s ?p ?o
}
"""
print(requete)
res = graphe2.query(requete)
#for i in res:
#    print(str(i[0]),str(i[1]))


prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?s ?p ?o
WHERE{
?s ?p ?o
}



In [69]:
top = "10"
requete = """
prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?nom ?prenom (count(?a2) as ?nb_con)
WHERE{
?s :knows ?a2 . 
?s :familyName ?nom . 
?s :givenName ?prenom . 

}
GROUP BY ?s
ORDER BY DESC(?nb_con)
LIMIT %t
""".replace("%t",top)

print(requete)
rez = graphe2.query(requete)
cpt = 1
D = {}
D["Acteur"] = []
D["Classement"] = []
D["Nombre de connaissances"] = []

for i in rez:
    print("-",end="")
    D["Acteur"].append(i[0] + " " + i[1])
    D["Classement"].append(cpt)
    D["Nombre de connaissances"].append(int(i[2]))
    cpt = cpt + 1
    
print("")
print("==TOP {}==".format(str(top)))
import pandas as pd
df = pd.DataFrame(D)
print(df)
print("=========")

print("==TOP {} STATS==".format(str(top)))
print(df.describe()["Nombre de connaissances"])
print("=========")


prefix ns1: <http://xmlns.com/foaf/0.1/> 
prefix : <http://test.org/onto.owl#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
SELECT DISTINCT ?nom ?prenom (count(?a2) as ?nb_con)
WHERE{
?s :knows ?a2 . 
?s :familyName ?nom . 
?s :givenName ?prenom . 

}
GROUP BY ?s
ORDER BY DESC(?nb_con)
LIMIT 10

----------
==TOP 10==
                   Acteur  Classement  Nombre de connaissances
0           Pearce Pevita           1                       23
1          Doyle Iretiola           2                       21
2            Peña Michael           3                       20
3              Riggle Rob           4                       19
4  Moore Stephen Campbell           5                       19
5             Kosoko Jide           6                       19
6            Friedle Will           7                       18
7            Cullen Peter           8                       18
8     Dhanasevi Chantavit           9       